# Segmenting and Clustering Neighborhoods in Toronto


<blockquote>In this assignment, I will try to explore, segment, and cluster the neighborhoods in the city of Toronto based on the postalcode and borough information.</blockquote>


### 1. Import Libraries

In [1]:
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import numpy as np # library to handle data in a vectorized manner
from bs4 import BeautifulSoup # this module helps in web scrapping.
import requests  # library to handle requests
import json # library to handle JSON files
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import pgeocode # convert an postcod into latitude and longitude values
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

### 2. Downloading and Prepping Data

The neighborhood data is not available online. So let's load and scrape the __[Wikipedia page](https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M)__, wich has all the information we need to explore and cluster the neighborhoods in Toronto, in order to obtain the data that is in the table of postal codes and to transform the data into a pandas  dataframe.

#### 2.1 Download the contents of the web page

In [2]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"

#### 2.2 Scrape data from HTML tables into a DataFrame
> Use the **read_html** function to directly get DataFrames from the url.
> Use the **match** parameter to select the specific table we want. 
> If the table contains a string matching the text it will be read.

In [3]:
df_Toronto = pd.read_html(url, match="Neighbourhood", flavor='bs4')[0]
df_Toronto.columns = ['PostalCode', 'Borough', 'Neighborhood']
df_Toronto.head()

PostalCode           Borough               Neighborhood
0        M1A      Not assigned               Not assigned
1        M2A      Not assigned               Not assigned
2        M3A        North York                  Parkwoods
3        M4A        North York           Victoria Village
4        M5A  Downtown Toronto  Regent Park, Harbourfront

The dataframe must meet the following conditions:
- The dataframe will consist of three columns: PostalCode, Borough, and Neighborhood.
- Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned.
- If a cell has a borough but a *Not assigned*  neighborhood, then the neighborhood will be the same as the borough.

#### 2.3  Identify and handle missing values
As we can see, that DataFrame have missing values which represented by *Not assigned*. We will drop the whole row with them.

In [4]:
df_Toronto.Borough.replace("Not assigned", np.nan, inplace = True) # replace "Not assigned" to NaN(Not a Number)
df_Toronto.dropna(subset=["Borough"], axis=0, inplace=True) # Drop missing values along the column "Borough"
df_Toronto.reset_index(drop=True, inplace=True) # Reset index, if we droped some rows
df_Toronto.head()

PostalCode           Borough                                 Neighborhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [5]:
df_Toronto.shape

(103, 3)

In [6]:
df_Toronto.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 103 entries, 0 to 102
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   PostalCode    103 non-null    object
 1   Borough       103 non-null    object
 2   Neighborhood  103 non-null    object
dtypes: object(3)
memory usage: 2.5+ KB


#### 2.4 Get the latitude and the longitude coordinates of each Postal Code
In this step we use **pgeocode** library.

In [7]:
geolocator = pgeocode.Nominatim('ca')
postal_codes = df_Toronto['PostalCode'].tolist()
latitude = []
longitude = []

for i, postal_code in enumerate(postal_codes):
    g = geolocator.query_postal_code(postal_code)
    if not g.empty:
        latitude.append(g.latitude)
        longitude.append(g.longitude)

In [8]:
len(latitude)

103

When the geographical coordinates of the Toronto districts are received, add them to the dataframe.

In [9]:
df_Toronto['Latitude'] = latitude
df_Toronto['Longitude'] = longitude
df_Toronto.head(10)

PostalCode           Borough                                 Neighborhood  \
0        M3A        North York                                    Parkwoods   
1        M4A        North York                             Victoria Village   
2        M5A  Downtown Toronto                    Regent Park, Harbourfront   
3        M6A        North York             Lawrence Manor, Lawrence Heights   
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   
5        M9A         Etobicoke      Islington Avenue, Humber Valley Village   
6        M1B       Scarborough                               Malvern, Rouge   
7        M3B        North York                                    Don Mills   
8        M4B         East York              Parkview Hill, Woodbine Gardens   
9        M5B  Downtown Toronto                     Garden District, Ryerson   

   Latitude  Longitude  
0   43.7545   -79.3300  
1   43.7276   -79.3148  
2   43.6555   -79.3626  
3   43.7223   -79.4504  
4   43.6641   -79.3889  
5   43.6662   -79.5282  
6   43.8113   -79.1930  
7   43.7450   -79.3590  
8   43.7063   -79.3094  
9   43.6572   -79.3783

Let's delete the lines with the **NaN** value, as they can interfere with the construction of the map.

In [10]:
df_Toronto.dropna(subset=["Latitude"], axis=0, inplace=True)
df_Toronto.reset_index(drop=True, inplace=True)

#### 2.5 Split naighborhoods in the column Neighborhood.

More than one neighborhood can exist in one postal code area. 
In the DataFrame they combined into one row and separated with a comma. We will separate them for the convenience of later analysis.

In [11]:
df_Toronto['Neighborhood'] = df_Toronto['Neighborhood'].str.split(', ') # Converting each line to a list separated by comma 

In [12]:
df_Toronto.head()

PostalCode           Borough                                   Neighborhood  \
0        M3A        North York                                    [Parkwoods]   
1        M4A        North York                             [Victoria Village]   
2        M5A  Downtown Toronto                    [Regent Park, Harbourfront]   
3        M6A        North York             [Lawrence Manor, Lawrence Heights]   
4        M7A  Downtown Toronto  [Queen's Park, Ontario Provincial Government]   

   Latitude  Longitude  
0   43.7545   -79.3300  
1   43.7276   -79.3148  
2   43.6555   -79.3626  
3   43.7223   -79.4504  
4   43.6641   -79.3889

Use the **apply function**, which can be substituted for both aggregate and transform in many standard use cases. **GroupBy** will examine the results of the apply step and try to return a sensibly combined result if it doesn’t fit into either of the above two categories.

In [13]:
# Create new DataFrame with splited neighborhoods and take each neighborhood in own row.
df_Toronto_new = df_Toronto.groupby('PostalCode').Neighborhood.apply(lambda x: pd.DataFrame([item for sublist in x.values for item in sublist])).reset_index().drop('level_1', axis = 1)
df_Toronto_new.columns = ['PostalCode', 'Neighborhood'] # Add new names for columns.
df_Toronto.drop(["Neighborhood"], axis=1, inplace=True) # Drop old column Neighborhood
df_Toronto1 = pd.merge(df_Toronto, df_Toronto_new, on='PostalCode', sort=True) # Merge old and new DataFrames.

In [14]:
df_Toronto1.head()

PostalCode      Borough  Latitude  Longitude    Neighborhood
0        M1B  Scarborough   43.8113   -79.1930         Malvern
1        M1B  Scarborough   43.8113   -79.1930           Rouge
2        M1C  Scarborough   43.7878   -79.1564      Rouge Hill
3        M1C  Scarborough   43.7878   -79.1564      Port Union
4        M1C  Scarborough   43.7878   -79.1564  Highland Creek

In [15]:
df_Toronto1.shape

(216, 5)

### 3. Explore and cluster the neighborhoods

#### 3.1 Explore data

In [16]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df_Toronto1['Borough'].unique()),
        df_Toronto1.shape[0]))

The dataframe has 9 boroughs and 216 neighborhoods.


In [17]:
address = 'Toronto'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [18]:
# create map of New York using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_Toronto1['Latitude'], df_Toronto1['Longitude'], df_Toronto1['Borough'], df_Toronto1['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker([lat, lng], radius=5, popup=label, color='blue', fill=True, fill_color='#3186cc', fill_opacity=0.7, parse_html=False).add_to(map_toronto)  
    
map_toronto

#### 3.2 Utilizing the Foursquare API 

In [ ]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

In [20]:
def getNearbyVenues(names, latitudes, longitudes, radius=700):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [21]:
toronto_venues = getNearbyVenues(names=df_Toronto1['Neighborhood'],
                                   latitudes=df_Toronto1['Latitude'],
                                   longitudes=df_Toronto1['Longitude'])
print(toronto_venues.shape)
toronto_venues.head()

(7146, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Malvern                43.8113                 -79.193   
1      Malvern                43.8113                 -79.193   
2      Malvern                43.8113                 -79.193   
3      Malvern                43.8113                 -79.193   
4        Rouge                43.8113                 -79.193   

                  Venue  Venue Latitude  Venue Longitude        Venue Category  
0               Wendy’s       43.807448       -79.199056  Fast Food Restaurant  
1     Upper Rouge Trail       43.809988       -79.186147                 Trail  
2         Moose Exhibit       43.816823       -79.193432           Zoo Exhibit  
3  Grizzly Bear Exhibit       43.817031       -79.193458           Zoo Exhibit  
4               Wendy’s       43.807448       -79.199056  Fast Food Restaurant

In [22]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))
toronto_venues.groupby('Neighborhood').count().head()

There are 308 uniques categories.


Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                            
Adelaide                           100                     100    100   
Agincourt                           18                      18     18   
Agincourt North                      5                       5      5   
Albion Gardens                      14                      14     14   
Alderwood                            9                       9      9   

                 Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                      
Adelaide                    100              100             100  
Agincourt                    18               18              18  
Agincourt North               5                5               5  
Albion Gardens               14               14              14  
Alderwood                     9                9               9

#### 3.3 Analyze Each Neighborhood

In [23]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[179]] + list(toronto_onehot.columns[:179]) + list(toronto_onehot.columns[180:])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Market  Accessories Store  Adult Boutique  Afghan Restaurant  \
0       0                  0               0                  0   
1       0                  0               0                  0   
2       0                  0               0                  0   
3       0                  0               0                  0   
4       0                  0               0                  0   

   African Restaurant  Airport  American Restaurant  Animal Shelter  \
0                   0        0                    0               0   
1                   0        0                    0               0   
2                   0        0                    0               0   
3                   0        0                    0               0   
4                   0        0                    0               0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Dealership  Auto Garage  \
0                 0                   0                0            0   
1                 0                   0                0            0   
2                 0                   0                0            0   
3                 0                   0                0            0   
4                 0                   0                0            0   

   Automotive Shop  BBQ Joint  Baby Store  Badminton Court  Bagel Shop  \
0                0          0           0                0           0   
1                0          0           0                0           0   
2                0          0           0                0           0   
3                0          0           0                0           0   
4                0          0           0                0           0   

   Bakery  Bank  Bar  Baseball Field  Basketball Stadium  Beach Bar  Beer Bar  \
0       0     0    0               0                   0          0         0   
1       0     0    0               0                   0          0         0   
2       0     0    0               0                   0          0         0   
3       0     0    0               0                   0          0         0   
4       0     0    0               0                   0          0         0   

   Beer Store  Belgian Restaurant  Bistro  Board Shop  Boat or Ferry  \
0           0                   0       0           0              0   
1           0                   0       0           0              0   
2           0                   0       0           0              0   
3           0                   0       0           0              0   
4           0                   0       0           0              0   

   Bookstore  Botanical Garden  Boutique  Brazilian Restaurant  \
0          0                 0         0                     0   
1          0                 0         0                     0   
2          0                 0         0                     0   
3          0                 0         0                     0   
4          0                 0         0                     0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Buffet  Burger Joint  \
0               0        0                0       0             0   
1               0        0                0       0             0   
2               0        0                0       0             0   
3               0        0                0       0             0   
4               0        0                0       0             0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Business Service  Butcher  \
0              0         0

Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [24]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood    Market  \
0                                         Adelaide  0.000000   
1                                        Agincourt  0.000000   
2                                  Agincourt North  0.000000   
3                                   Albion Gardens  0.000000   
4                                        Alderwood  0.000000   
5                                   Bathurst Manor  0.000000   
6                                    Bathurst Quay  0.011364   
7                                  Bayview Village  0.000000   
8                                 Beaumond Heights  0.000000   
9                                     Bedford Park  0.000000   
10                                     Berczy Park  0.000000   
11                                     Birch Cliff  0.000000   
12                               Bloordale Gardens  0.000000   
13                 Broadview North (Old East York)  0.000000   
14                                        Brockton  0.000000   
15           Business reply mail Processing Centre  0.000000   
16                                        CN Tower  0.011364   
17                                     Cabbagetown  0.014706   
18                             Caledonia-Fairbanks  0.000000   
19                                       Cedarbrae  0.000000   
20                              Central Bay Street  0.000000   
21                                       Chinatown  0.000000   
22                                        Christie  0.000000   
23                            Church and Wellesley  0.000000   
24                                        Clairlea  0.000000   
25                                  Clarks Corners  0.000000   
26                                      Cliffcrest  0.000000   
27                                       Cliffside  0.000000   
28                                  Cliffside West  0.000000   
29                                      Cloverdale  0.000000   
30                                  Commerce Court  0.000000   
31                                      Davisville  0.000000   
32                                Davisville North  0.000000   
33                                       Deer Park  0.000000   
34                                         Del Ray  0.000000   
35                                 Design Exchange  0.000000   
36                                       Don Mills  0.000000   
37                                     Dorset Park  0.000000   
38                              Dovercourt Village  0.000000   
39                                       Downsview  0.000000   
40                                 Downsview North  0.000000   
41                                        Dufferin  0.000000   
42                            East Birchmount Park  0.000000   
43                                    East Toronto  0.000000   
44                                           Emery  0.000000   
45                                        Eringate  0.000000   
46                                Exhibition Place  0.000000   
47                                        Fairview  0.000000   
48                            First Canadian Place  0.000000   
49                        Forest Hill North & West  0.000000   
50                           Forest Hill Road Park  0.000000   
51                                  Forest Hill SE  0.000000   
52                                 Garden District  0.000000   
53                                       Glencairn  0.000000   
54                                     Golden Mile  0.000000   
55                                     Grange Park  0.000000   
56                                       Guildwood  0.000000   
57                                         Harbord  0.000000   
58                                    Harbourfront  0.000000   
59                               Harbourfront East  0.000000   
60                               Harbourfront West  0.011364   
61                                      Henry Farm  0.000000   
62    

In [25]:
toronto_grouped.shape

(206, 308)

In [26]:
# Function to sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide           Coffee Shop                 Hotel   
1        Agincourt    Chinese Restaurant                Bakery   
2  Agincourt North              Pharmacy        Shopping Plaza   
3   Albion Gardens           Pizza Place         Grocery Store   
4        Alderwood           Pizza Place            Print Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Café            Restaurant               Theater   
1             Newsagent        Sandwich Place       Badminton Court   
2                   Gym                  Park          Intersection   
3  Caribbean Restaurant        Sandwich Place   Fried Chicken Joint   
4                   Pub           Gas Station        Sandwich Place   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Clothing Store   Japanese Restaurant                   Gym   
1                Lounge      Sushi Restaurant           Coffee Shop   
2           Zoo Exhibit     Electronics Store           Escape Room   
3           Video Store              Pharmacy  Fast Food Restaurant   
4                   Gym    Athletics & Sports           Coffee Shop   

  9th Most Common Venue       10th Most Common Venue  
0      Sushi Restaurant           Seafood Restaurant  
1         Grocery Store                Shopping Mall  
2  Ethiopian Restaurant                  Event Space  
3           Auto Garage                         Park  
4  Ethiopian Restaurant  Eastern European Restaurant

#### 3.4 Cluster Neighborhoods
Run k-means to cluster the neighborhood into 5 clusters.

In [27]:
# set number of clusters
kclusters = 9

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 3, 3, 3, 0, 0, 3, 3, 0], dtype=int32)

In [28]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [29]:
toronto_merged = df_Toronto1

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
toronto_merged = toronto_merged.fillna(0)
toronto_merged['Cluster Labels'] = toronto_merged['Cluster Labels'].astype(int)
toronto_merged.head()

PostalCode      Borough  Latitude  Longitude    Neighborhood  \
0        M1B  Scarborough   43.8113   -79.1930         Malvern   
1        M1B  Scarborough   43.8113   -79.1930           Rouge   
2        M1C  Scarborough   43.7878   -79.1564      Rouge Hill   
3        M1C  Scarborough   43.7878   -79.1564      Port Union   
4        M1C  Scarborough   43.7878   -79.1564  Highland Creek   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               8           Zoo Exhibit                 Trail   
1               8           Zoo Exhibit                 Trail   
2               1                  Park          Home Service   
3               1                  Park          Home Service   
4               1                  Park          Home Service   

  3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
0  Fast Food Restaurant  Eastern European Restaurant           Escape Room   
1  Fast Food Restaurant  Eastern European Restaurant           Escape Room   
2                   Bar            Fish & Chips Shop           Zoo Exhibit   
3                   Bar            Fish & Chips Shop           Zoo Exhibit   
4                   Bar            Fish & Chips Shop           Zoo Exhibit   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  Ethiopian Restaurant           Event Space    Falafel Restaurant   
1  Ethiopian Restaurant           Event Space    Falafel Restaurant   
2  Fast Food Restaurant  Ethiopian Restaurant           Event Space   
3  Fast Food Restaurant  Ethiopian Restaurant           Event Space   
4  Fast Food Restaurant  Ethiopian Restaurant           Event Space   

  9th Most Common Venue 10th Most Common Venue  
0                  Farm         Farmers Market  
1                  Farm         Farmers Market  
2    Falafel Restaurant                   Farm  
3    Falafel Restaurant                   Farm  
4    Falafel Restaurant                   Farm

Visualize the resulting clusters.

In [30]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

- Cluster 1

In [31]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
5                                        Guildwood           Pizza Place   
6                                      Morningside           Pizza Place   
7                                        West Hill           Pizza Place   
9                                        Cedarbrae           Gas Station   
14                                     Golden Mile              Bus Line   
15                                        Clairlea              Bus Line   
16                                        Oakridge              Bus Line   
17                                       Cliffside        Ice Cream Shop   
18                                      Cliffcrest        Ice Cream Shop   
19                        Scarborough Village West        Ice Cream Shop   
20                                     Birch Cliff                  Café   
21                                  Cliffside West                  Café   
25                                         Wexford            Hookah Bar   
26                                        Maryvale            Hookah Bar   
27                                       Agincourt    Chinese Restaurant   
37                                     Upper Rouge                     0   
38                               Hillcrest Village  Fast Food Restaurant   
39                                        Fairview        Clothing Store   
40                                      Henry Farm        Clothing Store   
41                                          Oriole        Clothing Store   
45                                      Willowdale           Coffee Shop   
46                                     Newtonbrook     Korean Restaurant   
47                                      Willowdale           Coffee Shop   
48                                 Willowdale East           Coffee Shop   
50                                      Willowdale           Coffee Shop   
55                                  Bathurst Manor           Coffee Shop   
56                                  Wilson Heights           Coffee Shop   
57                                 Downsview North           Coffee Shop   
67                                Woodbine Heights           Pizza Place   
68                                     The Beaches                   Pub   
69                                         Leaside     Electronics Store   
70                                Thorncliffe Park     Indian Restaurant   
73                               The Danforth West      Greek Restaurant   
74                                       Riverdale      Greek Restaurant   
75                                    India Bazaar     Indian Restaurant   
76                                The Beaches West     Indian Restaurant   
77                                 Studio District           Coffee Shop   
78                                   Lawrence Park           Coffee Shop   
80                              North Toronto West           Coffee Shop   
81                                   Lawrence Park           Coffee Shop   
82                                      Davisville          Dessert Shop   
85                                 Summerhill West          Skating Rink   
86                                       Rathnelly          Skating Rink   
87                                      South Hill          Skating Rink   
88                                  Forest Hill SE          Skating Rink   
89                                       Deer Park          Skating Rink   
91                                  St. James Town           Coffee Shop   
92                                     Cabbagetown           Coffee Shop   
93                            Church and Wellesley           Coffee Shop   
94                                     Regent Park           Coffee Shop   
95                                    Harbourfront           Coffee Shop   
96                                 Garden District           Coffee Shop   
97        

Examine each cluster and determine the discriminating venue categories that distinguish each cluster.

- Cluster 2

In [32]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
2                         Rouge Hill                  Park   
3                         Port Union                  Park   
4                     Highland Creek                  Park   
10               Scarborough Village                  Park   
49                   York Mills West                  Park   
52                         Parkwoods                  Park   
53                         Don Mills                  Park   
54                         Don Mills                  Park   
71                      East Toronto                  Park   
72   Broadview North (Old East York)                  Park   
90                          Rosedale                  Park   
138              Caledonia-Fairbanks                  Park   
147                       North Park          Home Service   
148                  Maple Leaf Park          Home Service   
149                      Upwood Park          Home Service   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
2            Home Service                   Bar     Fish & Chips Shop   
3            Home Service                   Bar     Fish & Chips Shop   
4            Home Service                   Bar     Fish & Chips Shop   
10      Indian Restaurant            Restaurant           Zoo Exhibit   
49      Convenience Store             Speakeasy           Zoo Exhibit   
52               Bus Stop     Food & Drink Shop          Intersection   
53           Gourmet Shop                   Gym          Intersection   
54           Gourmet Shop                   Gym          Intersection   
71         Breakfast Spot         Metro Station              Bus Line   
72         Breakfast Spot         Metro Station              Bus Line   
90            Flower Shop            Playground         Grocery Store   
138                  Café         Women's Store                Bakery   
147         Women's Store     Convenience Store                Bakery   
148         Women's Store     Convenience Store                Bakery   
149         Women's Store     Convenience Store                Bakery   

    5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
2             Zoo Exhibit  Fast Food Restaurant         Ethiopian Restaurant   
3             Zoo Exhibit  Fast Food Restaurant         Ethiopian Restaurant   
4             Zoo Exhibit  Fast Food Restaurant         Ethiopian Restaurant   
10         Farmers Market     Electronics Store                  Escape Room   
49   Fast Food Restaurant           Escape Room         Ethiopian Restaurant   
52            Zoo Exhibit  Fast Food Restaurant         Ethiopian Restaurant   
53           Soccer Field                  Farm  Eastern European Restaurant   
54           Soccer Field                  Farm  Eastern European Restaurant   
71     Italian Restaurant                  Food            Food & Drink Shop   
72     Italian Restaurant                  Food            Food & Drink Shop   
90          Historic Site          Skating Rink                  Candy Store   
138    Mexican Restaurant         Grocery Store                     Bus Stop   
147                  Park           Zoo Exhibit               Farmers Market   
148                  Park           Zoo Exhibit               Farmers Market   
149                  Park           Zoo Exhibit               Farmers Market   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
2             Event Space    Falafel Restaurant                   Farm  
3             Event Space    Falafel Restaurant                   Farm  
4             Event Space    Falafel Restaurant                   Farm  
10   Ethiopian Restaurant           Event Space     Falafel Restaurant  
49            Event Space    Falafel Restaurant                   Farm  
52            Event Space    Falafel Restaurant                   Farm  
53      Electronics Store           Escape Room   Ethiopian Restaurant




- Cluster 3

In [33]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
188   West Deane Park           Pizza Place                  Park   
189  Princess Gardens           Pizza Place                  Park   
190      Martin Grove           Pizza Place                  Park   
191         Islington           Pizza Place                  Park   
192        Cloverdale           Pizza Place                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
188     Fish & Chips Shop        Farmers Market     Electronics Store   
189     Fish & Chips Shop        Farmers Market     Electronics Store   
190     Fish & Chips Shop        Farmers Market     Electronics Store   
191     Fish & Chips Shop        Farmers Market     Electronics Store   
192     Fish & Chips Shop        Farmers Market     Electronics Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
188           Escape Room  Ethiopian Restaurant           Event Space   
189           Escape Room  Ethiopian Restaurant           Event Space   
190           Escape Room  Ethiopian Restaurant           Event Space   
191           Escape Room  Ethiopian Restaurant           Event Space   
192           Escape Room  Ethiopian Restaurant           Event Space   

    9th Most Common Venue 10th Most Common Venue  
188    Falafel Restaurant                   Farm  
189    Falafel Restaurant                   Farm  
190    Falafel Restaurant                   Farm  
191    Falafel Restaurant                   Farm  
192    Falafel Restaurant                   Farm

- Cluster 4


In [34]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  2nd Most Common Venue  \
31                   Milliken              Pharmacy         Shopping Plaza   
32            Agincourt North              Pharmacy         Shopping Plaza   
33               Steeles East              Pharmacy         Shopping Plaza   
34            L'Amoreaux East              Pharmacy         Shopping Plaza   
42            Bayview Village    Golf Driving Range            Flower Shop   
51            Willowdale West           Pizza Place         Discount Store   
60                  Downsview                 Hotel          Grocery Store   
61                  Downsview                 Hotel          Grocery Store   
62                  Downsview                 Hotel          Grocery Store   
63                  Downsview                 Hotel          Grocery Store   
64           Victoria Village           Pizza Place  Portuguese Restaurant   
65              Parkview Hill           Pizza Place              Pet Store   
66           Woodbine Gardens           Pizza Place              Pet Store   
79           Davisville North           Pizza Place                   Park   
83                 Moore Park                  Park        Thai Restaurant   
84            Summerhill East                  Park        Thai Restaurant   
114  Forest Hill North & West  Gym / Fitness Center                   Park   
115     Forest Hill Road Park  Gym / Fitness Center                   Park   
136                 Glencairn           Pizza Place          Grocery Store   
168                 Alderwood           Pizza Place             Print Shop   
169               Long Branch           Pizza Place             Print Shop   
200                    Weston              Pharmacy          Jewelry Store   
206             South Steeles           Pizza Place          Grocery Store   
207               Silverstone           Pizza Place          Grocery Store   
208                Humbergate           Pizza Place          Grocery Store   
209                 Jamestown           Pizza Place          Grocery Store   
210               Mount Olive           Pizza Place          Grocery Store   
211          Beaumond Heights           Pizza Place          Grocery Store   
212               Thistletown           Pizza Place          Grocery Store   
213            Albion Gardens           Pizza Place          Grocery Store   
214                 Northwest                 Hotel                    Gym   
215  West Humber - Clairville                 Hotel                    Gym   

    3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
31                    Gym                  Park           Intersection   
32                    Gym                  Park           Intersection   
33                    Gym                  Park           Intersection   
34                    Gym                  Park           Intersection   
42                   Park                 Trail       Asian Restaurant   
51            Coffee Shop             Juice Bar               Bus Line   
60            Coffee Shop                  Park  Vietnamese Restaurant   
61            Coffee Shop                  Park  Vietnamese Restaurant   
62            Coffee Shop                  Park  Vietnamese Restaurant   
63            Coffee Shop                  Park  Vietnamese Restaurant   
64           Hockey Arena     French Restaurant           Intersection   
65           Intersection             Gastropub   Gym / Fitness Center   
66           Intersection             Gastropub   Gym / Fitness Center   
79         Breakfast Spot              Gym Pool      Food & Drink Shop   
83          Grocery Store                   Gym                   Café   
84          Grocery Store                   Gym                   Café   
114                 Trail      Sushi Restaurant          Jewelry Store   
115                 Trail      Sushi Restaurant          Jewelry Store   
136                   Pub           

- Cluster 5

In [35]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8                      Woburn           Coffee Shop                  Park   
173            Old Mill South           Coffee Shop                  Park   
174          King's Mill Park           Coffee Shop                  Park   
175                  Sunnylea           Coffee Shop                  Park   
176                Humber Bay           Coffee Shop                  Park   
177                 Mimico NE           Coffee Shop                  Park   
178        The Queensway East           Coffee Shop                  Park   
179     Royal York South East           Coffee Shop                  Park   
180  Kingsway Park South East           Coffee Shop                  Park   

    3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
8        Business Service                  Zoo Exhibit  Fast Food Restaurant   
173                  Bank  Eastern European Restaurant        Ice Cream Shop   
174                  Bank  Eastern European Restaurant        Ice Cream Shop   
175                  Bank  Eastern European Restaurant        Ice Cream Shop   
176                  Bank  Eastern European Restaurant        Ice Cream Shop   
177                  Bank  Eastern European Restaurant        Ice Cream Shop   
178                  Bank  Eastern European Restaurant        Ice Cream Shop   
179                  Bank  Eastern European Restaurant        Ice Cream Shop   
180                  Bank  Eastern European Restaurant        Ice Cream Shop   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8    Ethiopian Restaurant           Event Space    Falafel Restaurant   
173           Flower Shop              Bus Stop    Italian Restaurant   
174           Flower Shop              Bus Stop    Italian Restaurant   
175           Flower Shop              Bus Stop    Italian Restaurant   
176           Flower Shop              Bus Stop    Italian Restaurant   
177           Flower Shop              Bus Stop    Italian Restaurant   
178           Flower Shop              Bus Stop    Italian Restaurant   
179           Flower Shop              Bus Stop    Italian Restaurant   
180           Flower Shop              Bus Stop    Italian Restaurant   

    9th Most Common Venue 10th Most Common Venue  
8                    Farm         Farmers Market  
173  Fast Food Restaurant         Farmers Market  
174  Fast Food Restaurant         Farmers Market  
175  Fast Food Restaurant         Farmers Market  
176  Fast Food Restaurant         Farmers Market  
177  Fast Food Restaurant         Farmers Market  
178  Fast Food Restaurant         Farmers Market  
179  Fast Food Restaurant         Farmers Market  
180  Fast Food Restaurant         Farmers Market

- Cluster 6

In [36]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 5, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
11           Kennedy Park           Coffee Shop    Light Rail Station   
12                Ionview           Coffee Shop    Light Rail Station   
13   East Birchmount Park           Coffee Shop    Light Rail Station   
28         Clarks Corners     Convenience Store           Pizza Place   
29          Tam O'Shanter     Convenience Store           Pizza Place   
30               Sullivan     Convenience Store           Pizza Place   
35           Steeles West        Cosmetics Shop                  Bank   
36        L'Amoreaux West        Cosmetics Shop                  Bank   
58         Northwood Park           Coffee Shop        Sandwich Place   
59        York University           Coffee Shop        Sandwich Place   
201             Westmount           Pizza Place        Discount Store   
202     Kingsview Village    Chinese Restaurant           Coffee Shop   
203          St. Phillips    Chinese Restaurant           Coffee Shop   
204  Martin Grove Gardens    Chinese Restaurant           Coffee Shop   
205      Richview Gardens    Chinese Restaurant           Coffee Shop   

    3rd Most Common Venue      4th Most Common Venue  \
11    Rental Car Location             Sandwich Place   
12    Rental Car Location             Sandwich Place   
13    Rental Car Location             Sandwich Place   
28               Pharmacy         Italian Restaurant   
29               Pharmacy         Italian Restaurant   
30               Pharmacy         Italian Restaurant   
35            Pizza Place                   Pharmacy   
36            Pizza Place                   Pharmacy   
58                    Bar                 Sports Bar   
59                    Bar                 Sports Bar   
201           Coffee Shop  Middle Eastern Restaurant   
202              Bus Line                Pizza Place   
203              Bus Line                Pizza Place   
204              Bus Line                Pizza Place   
205              Bus Line                Pizza Place   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
11              Discount Store         Grocery Store              Pharmacy   
12              Discount Store         Grocery Store              Pharmacy   
13              Discount Store         Grocery Store              Pharmacy   
28          Chinese Restaurant       Thai Restaurant           Gas Station   
29          Chinese Restaurant       Thai Restaurant           Gas Station   
30          Chinese Restaurant       Thai Restaurant           Gas Station   
35                 Coffee Shop  Other Great Outdoors        Sandwich Place   
36                 Coffee Shop  Other Great Outdoors        Sandwich Place   
58   Middle Eastern Restaurant           Pizza Place  Caribbean Restaurant   
59   Middle Eastern Restaurant           Pizza Place  Caribbean Restaurant   
201             Ice Cream Shop           Gas Station          Intersection   
202        American Restaurant              Pharmacy           Gas Station   
203        American Restaurant              Pharmacy           Gas Station   
204        American Restaurant              Pharmacy           Gas Station   
205        American Restaurant              Pharmacy           Gas Station   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
11           Intersection                  Bank            Pizza Place  
12           Intersection                  Bank            Pizza Place  
13           Intersection                  Bank            Pizza Place  
28         Sandwich Place           Coffee Shop           Noodle House  
29         Sandwich Place           Coffee Shop           Noodle House  
30         Sandwich Place           Coffee Shop           Noodle House  
35     Chinese Restaurant  Fast Food Restaurant        Bubble Tea Shop  
36     Chinese Restaurant  Fast Food Restaurant        Bubble Tea Shop  
58     Chinese Restaurant   Japanese Rest

- Cluster 7

In [37]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 6, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
43    York Mills                  Pool           Zoo Exhibit   
44  Silver Hills                  Pool           Zoo Exhibit   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
43                 Field           Escape Room  Ethiopian Restaurant   
44                 Field           Escape Room  Ethiopian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
43           Event Space    Falafel Restaurant                  Farm   
44           Event Space    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
43        Farmers Market   Fast Food Restaurant  
44        Farmers Market   Fast Food Restaurant

- Cluster 8

In [38]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 7, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
22              Dorset Park             Pet Store                Bakery   
23          Wexford Heights             Pet Store                Bakery   
24  Scarborough Town Centre             Pet Store                Bakery   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
22             Wine Shop    Light Rail Station           Coffee Shop   
23             Wine Shop    Light Rail Station           Coffee Shop   
24             Wine Shop    Light Rail Station           Coffee Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
22     Electronics Store           Zoo Exhibit  Ethiopian Restaurant   
23     Electronics Store           Zoo Exhibit  Ethiopian Restaurant   
24     Electronics Store           Zoo Exhibit  Ethiopian Restaurant   

   9th Most Common Venue 10th Most Common Venue  
22           Event Space     Falafel Restaurant  
23           Event Space     Falafel Restaurant  
24           Event Space     Falafel Restaurant

- Cluster 9

In [39]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 8, toronto_merged.columns[[4] + list(range(6, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0      Malvern           Zoo Exhibit                 Trail   
1        Rouge           Zoo Exhibit                 Trail   

  3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
0  Fast Food Restaurant  Eastern European Restaurant           Escape Room   
1  Fast Food Restaurant  Eastern European Restaurant           Escape Room   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  Ethiopian Restaurant           Event Space    Falafel Restaurant   
1  Ethiopian Restaurant           Event Space    Falafel Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0                  Farm         Farmers Market  
1                  Farm         Farmers Market